In [ ]:
#TODO: Create a .py script

# Imports

In [1]:
import pandas as pd
import networkx as nx
import matplotlib.pyplot as plt
import numpy as np
import warnings

from sklearn.decomposition import PCA
from sklearn.preprocessing import normalize 
from numpy.linalg import norm

# Configuration

In [2]:
pd.set_option('display.max_rows', 2000)
pd.set_option('display.max_columns', 5000)
pd.set_option('display.max_colwidth', 5000)


warnings.filterwarnings('ignore')

In [46]:
native_mexican_entities = ['Agave', 'Allspice', 'Amaranth', 'Avocado', 'Beans', 'Bitter Orange', 'Byrsonima crassifolia', 'Capsicum', 'Chayote', 'Chia', 'Cocoa', 'Cocoa butter', 'Cocoa powder', 'Corn', 'Epazote', 'Green zucchini', 'Guava', 'Jackfruit', 'Jalapeno', 'Jicama', 'Mexican groundcherry', 'Mexican oregano', 'Nance', 'Narrowleaf cattail', 'Nopal', 'Papaya', 'Prickly Pear', 'Purslane', 'Sapodilla', 'Soursop', 'Spirulina', 'Tomato', 'Tortilla', 'Vanilla', 'Yam', 'Yautia']



# Read data

In [42]:
edamam_flavor = pd.read_pickle('../data/raw/edamam_flavor_dbs_nutrients.pkl')

# Functions

In [4]:
def cosine_similarity(w1, w2, base_df):
    A = base_df.loc[w1]
    B = base_df.loc[w2]
    cosine = np.dot(A,B)/(norm(A)*norm(B))
    return cosine

def jaccard_similarity(w1, w2, base_df):
    set1 = base_df.loc[w1].common_name
    set2 = base_df.loc[w2].common_name
    intersection = len(set1.intersection(set2))
    union = len(set1.union(set2))
    return intersection / union

def get_similar_ingredients(w, base_df):
    similarities = []
    relative_base_df = base_df.loc[base_df.index!=w]
    ingredients = pd.Series(relative_base_df.index)
    similarity = ingredients.apply(lambda x: cosine_similarity(w, x, base_df))
    answers = pd.DataFrame(similarity)
    return answers.set_index(relative_base_df.index).rename(columns={'entity_alias_readable': w})
     

def get_top_similarities(w, base_df, similarity_metric='jaccard'):
    similarities = []
    words = graph_flavor_molecules_df[graph_flavor_molecules_df.entity_alias_readable != w].entity_alias_readable.drop_duplicates()
    for entity in words:
        if similarity_metric == 'jaccard':
            similarities.append(jaccard_similarity(w, entity, base_df=base_df))
        elif similarity_metric == 'cosine':
            similarities.append(cosine_similarity(w, entity, base_df=base_df))
    response = pd.DataFrame({'entity':words, 'similarity':similarities})
    return  response.sort_values('similarity', ascending=False)

In [5]:
columns_defined = [
    'taste',
    'functional_groups',
    'fooddb_flavor_profile',
    'supersweetdb_id',
    'fooddb_id',
    'common_name',
    'bitterdb_id',
    'super_sweet',
    'flavornet_id',
    'pubchem_id',
    'bitter',
    'iupac_name',
    'odor',
    'smile',
    'inchi',
    'cas_id',
    'flavor_profile',
    'fema_flavor_profile',
]
flavor_molecules_df_list = []

nutrition_facts_df_list = []

for row_index in range(edamam_flavor.shape[0]):
    df_temporal_index = edamam_flavor.iloc[row_index]
    flavor_molecules_df = pd.DataFrame(df_temporal_index.molecules)
    flavor_molecules_df['entity_alias_readable'] = df_temporal_index.entity_alias_readable
    flavor_molecules_df_list.append(flavor_molecules_df)
    nutrition_facts_df = pd.DataFrame(df_temporal_index.nutritional_info).iloc[-1:]
    nutrition_facts_df['entity_alias_readable'] = df_temporal_index.entity_alias_readable
    nutrition_facts_df_list.append(nutrition_facts_df)
    
    
flavor_molecules = pd.concat(flavor_molecules_df_list)[columns_defined + ['entity_alias_readable']]
nutrition_facts = pd.concat(nutrition_facts_df_list).set_index("entity_alias_readable").fillna(0)

In [14]:
nutrition_facts_transformed = nutrition_facts.T
nutrition_facts_transformed = pd.DataFrame(
    normalize(nutrition_facts_transformed), 
    index=nutrition_facts_transformed.index,
    columns=nutrition_facts_transformed.columns
).T

In [20]:
flavor_molecules['list_flavor_profile'] = flavor_molecules.flavor_profile.str.split('@')
flavor_molecules['list_functional_groups'] = flavor_molecules.functional_groups.str.split('@')

In [34]:
molecules = flavor_molecules[['entity_alias_readable', 'inchi']]
molecules['dummy'] = 1
molecules = molecules.groupby(['entity_alias_readable', 'inchi']).count().reset_index()
molecules = pd.pivot_table(
    molecules, 
    index='entity_alias_readable',
    columns='inchi', 
    aggfunc='sum', 
    values="dummy", 
    fill_value=0
)
molecules_pca_obj = PCA(
    n_components=100,
    copy=True, 
    whiten=False,
    svd_solver='auto',
    tol=0.0, 
    iterated_power='auto',
    n_oversamples=10,
    power_iteration_normalizer='auto', 
    random_state=99
)

molecules_per_entity_reduced = pd.DataFrame((molecules_pca_obj.fit_transform(molecules)), index=molecules.index)


In [35]:
flavor_molecules[['entity_alias_readable', 'list_functional_groups']].explode('list_functional_groups')

entity_alias_readable                list_functional_groups
0                    Egg                                 amine
0                    Egg                         primary amine
0                    Egg  primary aliphatic amine (alkylamine)
0                    Egg            carboxylic acid derivative
0                    Egg                       carboxylic acid
..                   ...                                   ...
98      Japanese pumpkin                              aldehyde
99      Japanese pumpkin                      hydroxy compound
99      Japanese pumpkin                               alcohol
99      Japanese pumpkin                       primary alcohol
99      Japanese pumpkin                                alkene

[195096 rows x 2 columns]

In [36]:
functional_groups = flavor_molecules[['entity_alias_readable', 'list_functional_groups']].explode('list_functional_groups')
functional_groups['dummy'] = 1
functional_groups = functional_groups.groupby(['entity_alias_readable', 'list_functional_groups']).count().reset_index()

functional_groups = pd.pivot_table(
    functional_groups, 
    index='entity_alias_readable',
    columns='list_functional_groups', 
    aggfunc='sum', 
    values="dummy", 
    fill_value=0
)
functional_groups_pca_obj = PCA(
    n_components=20,
    copy=True, 
    whiten=False,
    svd_solver='auto',
    tol=0.0, 
    iterated_power='auto',
    n_oversamples=10,
    power_iteration_normalizer='auto', 
    random_state=99
)

functional_groups_per_entity_reduced = pd.DataFrame((functional_groups_pca_obj.fit_transform(functional_groups)), index=functional_groups.index)

In [37]:
functional_groups_per_entity_reduced

0           1          2          3   \
entity_alias_readable                                                       
Abalone                       27.836259  -12.453556   4.845235  -6.155267   
Abiyuch                       26.336626  -12.124318   4.252430  -6.109671   
Acerola                       27.836259  -12.453556   4.845235  -6.155267   
Acorn                         27.836259  -12.453556   4.845235  -6.155267   
Adzuki bean                   33.371709  -12.944513   6.482946  -6.333078   
Agar                          27.836259  -12.453556   4.845235  -6.155267   
Agave                         27.836259  -12.453556   4.845235  -6.155267   
Alaska blackfish             -68.538173    0.337993  -2.070029   1.924455   
Alaska pollock               -66.322606    0.597424  -1.476111   1.149960   
Alaska wild rhubarb           27.836259  -12.453556   4.845235  -6.155267   
Albacore tuna                -66.721071   -0.242797  -1.646793   1.234338   
Alfalfa                       33.434617  -13.498834   7.105266  -5.829070   
Allspice                      66.627471  -21.685404 -31.187856   6.069951   
Almond                        70.650826  -18.974344  18.720055   3.863870   
Alpinia                      -69.141984    0.349105  -3.220026   2.829921   
Amaranth                      28.234724  -11.613335   5.015917  -6.239645   
American butterfish           27.836259  -12.453556   4.845235  -6.155267   
American shad                -66.721071   -0.242797  -1.646793   1.234338   
Anchovy                      -66.306880    0.577319  -1.459858   1.130134   
Anise                         69.927029  -23.728097 -10.607545   9.952612   
Annual wild rice              26.336626  -12.124318   4.252430  -6.109671   
Apple                        170.039799  110.544698  -2.239388 -19.640166   
Apple Brandy                 -13.365947   38.566996  -2.864849   0.698724   
Apple Cider Vinegar          -51.347616    6.570490  -0.153543  -1.127698   
Apple Sauce                  -68.456082    0.141586  -2.588964   0.605319   
Apricot                      111.558528   47.280194  -1.925661  -0.194164   
Arabica coffee               -56.856227   -2.734466  -0.322883   1.140864   
Arrowhead                     27.836259  -12.453556   4.845235  -6.155267   
Arrowroot                     31.112010  -12.759653   6.097501  -6.320044   
Artichoke                     38.953081  -12.285091   4.417376  -5.924725   
Asafoetida                   -52.642726   -2.980570 -28.848823  10.261950   
Ascidians                    -66.721071   -0.242797  -1.646793   1.234338   
Asparagus                     92.396948  -19.921527  17.267776   6.424697   
Atlantic croaker             -66.721071   -0.242797  -1.646793   1.234338   
Atlantic halibut             -66.306880    0.577319  -1.459858   1.130134   
Atlantic herring              27.836259  -12.453556   4.845235  -6.155267   
Atlantic mackerel            -66.721071   -0.242797  -1.646793   1.234338   
Atlantic menhaden            -66.721071   -0.242797  -1.646793   1.234338   
Atlantic pollock             -66.721071   -0.242797  -1.646793   1.234338   
Atlantic salmon              -65.983446    1.218701  -1.373472   1.024282   
Atlantic wolffish            -64.807246    0.248081  -0.867052   1.084538   
Avocado                       68.218778   -5.643488   5.065895  -6.524729   
Babaco                       -59.320221   19.208157  -5.228667   4.808995   
Babassu palm                  27.836259  -12.453556   4.845235  -6.155267   
Bagel                        -65.983446    1.218701  -1.373472   1.024282   
Bakery Products              -66.345008   -0.577271   1.300275   7.068334   
Bamboo shoots                 29.750083  -11.962678   5.624976  -6.305066   
Banana                       107.433581   53.303036  -2.427094 -18.805738   
Barley                        67.344350  -12.195997  26.935308  11.024061   
Bartlett Pear                -39.219168   27.828337 -10.392585  -1.712893   
Basil                        116.

In [38]:
# NEW FLAVOR PROFILE OBTENSION
flavor_profiles = flavor_molecules[['entity_alias_readable', 'list_flavor_profile']].explode('list_flavor_profile')
flavor_profiles['dummy'] = 1
flavor_profiles = flavor_profiles.groupby(['entity_alias_readable', 'list_flavor_profile']).count().reset_index()

flavor_profiles = pd.pivot_table(
    flavor_profiles, 
    index='entity_alias_readable',
    columns='list_flavor_profile', 
    aggfunc='sum', 
    values="dummy", 
    fill_value=0
)

flavor_profile_pca_obj = PCA(
    n_components=100,
    copy=True, 
    whiten=False,
    svd_solver='auto',
    tol=0.0, 
    iterated_power='auto',
    n_oversamples=10,
    power_iteration_normalizer='auto', 
    random_state=99
)

flavor_profile_per_entity_reduced = pd.DataFrame((flavor_profile_pca_obj.fit_transform(flavor_profiles)), index=flavor_profiles.index)


In [39]:
general_flavor = pd.concat([flavor_profile_per_entity_reduced, functional_groups_per_entity_reduced, molecules_per_entity_reduced], axis=1)

general_flavor_pca_obj = PCA(
    n_components=50,
    copy=True, 
    whiten=False,
    svd_solver='auto',
    tol=0.0, 
    iterated_power='auto',
    n_oversamples=10,
    power_iteration_normalizer='auto', 
    random_state=99
)

general_flavor_per_entity_reduced = pd.DataFrame(general_flavor_pca_obj.fit_transform(normalize(general_flavor)), index=general_flavor.index)
general_flavor_per_entity_reduced

0         1         2         3         4   \
entity_alias_readable                                                           
Abalone                     -0.893551 -0.321017 -0.094985 -0.007072 -0.071476   
Abiyuch                     -0.885641 -0.322989 -0.092483 -0.005689 -0.104249   
Acerola                     -0.893551 -0.321017 -0.094985 -0.007072 -0.071476   
Acorn                       -0.893551 -0.321017 -0.094985 -0.007072 -0.071476   
Adzuki bean                 -0.905575 -0.291223 -0.097593 -0.029010  0.053047   
Agar                        -0.893551 -0.321017 -0.094985 -0.007072 -0.071476   
Agave                       -0.893551 -0.321017 -0.094985 -0.007072 -0.071476   
Alaska blackfish             0.996909 -0.086417  0.008316 -0.024144  0.005975   
Alaska pollock               0.996578 -0.087926 -0.001663 -0.024405  0.007760   
Alaska wild rhubarb         -0.893551 -0.321017 -0.094985 -0.007072 -0.071476   
Albacore tuna                0.995178 -0.097196  0.004549 -0.023270  0.006045   
Alfalfa                     -0.903244 -0.298948 -0.102745 -0.006372  0.029232   
Allspice                    -0.808043  0.095443  0.546862 -0.028304 -0.031513   
Almond                      -0.915543 -0.103331 -0.020149  0.098994  0.285000   
Alpinia                      0.996293 -0.076266  0.024281 -0.023834  0.002746   
Amaranth                    -0.901195 -0.298378 -0.108202 -0.009351 -0.067558   
American butterfish         -0.893551 -0.321017 -0.094985 -0.007072 -0.071476   
American shad                0.995178 -0.097196  0.004549 -0.023270  0.006045   
Anchovy                      0.996313 -0.088033 -0.002670 -0.024537  0.008818   
Anise                       -0.879100 -0.030218  0.389860  0.010253  0.084811   
Annual wild rice            -0.885641 -0.322989 -0.092483 -0.005689 -0.104249   
Apple                       -0.767122  0.630198 -0.091746 -0.225765  0.041964   
Apple Brandy                 0.190576  0.876551 -0.151810 -0.342902  0.083653   
Apple Cider Vinegar          0.964100 -0.051080 -0.040410 -0.148663  0.159764   
Apple Sauce                  0.996099 -0.086515  0.008660 -0.024992 -0.013114   
Apricot                     -0.835002  0.536594  0.017369 -0.167065  0.045919   
Arabica coffee               0.964261 -0.126695  0.036879 -0.039155  0.114124   
Arrowhead                   -0.893551 -0.321017 -0.094985 -0.007072 -0.071476   
Arrowroot                   -0.903362 -0.300111 -0.096543 -0.017279 -0.008524   
Artichoke                   -0.934669 -0.190271 -0.062644  0.022424 -0.053788   
Asafoetida                   0.868646  0.023126  0.469347 -0.047447 -0.056324   
Ascidians                    0.995178 -0.097196  0.004549 -0.023270  0.006045   
Asparagus                   -0.929735  0.108702  0.014338  0.229154  0.146645   
Atlantic croaker             0.995178 -0.097196  0.004549 -0.023270  0.006045   
Atlantic halibut             0.996313 -0.088033 -0.002670 -0.024537  0.008818   
Atlantic herring            -0.893551 -0.321017 -0.094985 -0.007072 -0.071476   
Atlantic mackerel            0.995178 -0.097196  0.004549 -0.023270  0.006045   
Atlantic menhaden            0.995178 -0.097196  0.004549 -0.023270  0.006045   
Atlantic pollock             0.995178 -0.097196  0.004549 -0.023270  0.006045   
Atlantic salmon              0.996811 -0.084254 -0.004768 -0.027720  0.009486   
Atlantic wolffish            0.994183 -0.096849 -0.006478 -0.025504  0.021907   
Avocado                     -0.960066  0.061234 -0.011736 -0.061100  0.129678   
Babaco                       0.978851  0.193798 -0.025051 -0.097855 -0.033268   
Babassu palm                -0.893551 -0.321017 -0.094985 -0.007072 -0.071476   
Bagel                        0.996811 -0.084254 -0.004768 -0.027720  0.009486   
Bakery Products              0.986959 -0.071985  0.008104  0.065446  0.074609   
Bamboo shoots               -0.902721 -0.294247 -0.110957 -0.010760 -0.034663   
Banana                      -0.805988  0.555695 -0.091056 -0.21884

In [40]:
food_characteristics = pd.concat([general_flavor_per_entity_reduced, nutrition_facts_transformed], axis=1)
food_characteristics.columns = food_characteristics.columns.astype(str)
food_characteristics_pca_obj = PCA(
    n_components=50,
    copy=True, 
    whiten=False,
    svd_solver='auto',
    tol=0.0, 
    iterated_power='auto',
    n_oversamples=10,
    power_iteration_normalizer='auto', 
    random_state=99
)

food_characteristics_per_entity_reduced = pd.DataFrame(food_characteristics_pca_obj.fit_transform(food_characteristics), index=general_flavor.index)

In [41]:
food_characteristics_per_entity_reduced

0         1         2         3         4   \
entity_alias_readable                                                           
Abalone                     -0.891945 -0.318960 -0.104537 -0.000254 -0.073866   
Abiyuch                     -0.885807 -0.321590 -0.103367 -0.014433 -0.101602   
Acerola                     -0.898564 -0.324697 -0.097180 -0.026225 -0.093648   
Acorn                       -0.893862 -0.321316 -0.093526  0.003481 -0.068527   
Adzuki bean                 -0.906379 -0.292469 -0.100999 -0.028090  0.054130   
Agar                        -0.894339 -0.320292 -0.103279 -0.011241 -0.069595   
Agave                       -0.891842 -0.321627 -0.109668 -0.031531 -0.054858   
Alaska blackfish             0.997873 -0.086741  0.003961 -0.025645  0.006392   
Alaska pollock               0.996993 -0.086551 -0.010172 -0.029885  0.006763   
Alaska wild rhubarb         -0.893545 -0.319089 -0.107913 -0.014899 -0.070801   
Albacore tuna                0.994864 -0.096370 -0.003677 -0.034514  0.004824   
Alfalfa                     -0.902790 -0.296622 -0.117677 -0.013941  0.028046   
Allspice                    -0.809978  0.092777  0.553154 -0.039976 -0.033893   
Almond                      -0.915556 -0.103942  0.005809  0.139248  0.277974   
Alpinia                      0.995173 -0.077239  0.021672 -0.035553  0.006820   
Amaranth                    -0.902363 -0.299981 -0.087493  0.008408 -0.064265   
American butterfish         -0.891441 -0.318625 -0.105704  0.002229 -0.074982   
American shad                0.996999 -0.097869  0.003700 -0.014462  0.005044   
Anchovy                      0.999286 -0.090357  0.006468 -0.005977  0.007207   
Anise                       -0.880569 -0.031779  0.424414  0.019043  0.081049   
Annual wild rice            -0.886215 -0.326159 -0.076551  0.012825 -0.097634   
Apple                       -0.766936  0.630324 -0.103285 -0.234292  0.045470   
Apple Brandy                 0.190585  0.876515 -0.160187 -0.350667  0.089692   
Apple Cider Vinegar          0.963434 -0.050605 -0.050533 -0.160733  0.157647   
Apple Sauce                  0.995288 -0.086553 -0.000483 -0.040486 -0.009663   
Apricot                     -0.834892  0.536553  0.003954 -0.177869  0.048615   
Arabica coffee               0.963593 -0.126233  0.025439 -0.054726  0.113640   
Arrowhead                   -0.893761 -0.321083 -0.097768 -0.007610 -0.067866   
Arrowroot                   -0.906225 -0.303415 -0.091064 -0.008993 -0.004255   
Artichoke                   -0.935339 -0.190037 -0.068079  0.019011 -0.051655   
Asafoetida                   0.859224  0.015142  0.609773 -0.031016 -0.067521   
Ascidians                    0.994700 -0.096398 -0.004240 -0.036254  0.006047   
Asparagus                   -0.930028  0.108789  0.008171  0.216282  0.151148   
Atlantic croaker             0.996298 -0.097294  0.000649 -0.021684  0.005082   
Atlantic halibut             1.001141 -0.090589 -0.004300 -0.008871  0.004714   
Atlantic herring            -0.888828 -0.319233 -0.107159  0.009321 -0.080531   
Atlantic mackerel            1.000005 -0.099749  0.002516 -0.008019  0.002147   
Atlantic menhaden            0.995677 -0.097065  0.000025 -0.025959  0.006353   
Atlantic pollock             0.996568 -0.096884  0.000774 -0.021648  0.003448   
Atlantic salmon              0.998090 -0.085767 -0.000407 -0.018270  0.008631   
Atlantic wolffish            0.994852 -0.096569 -0.009867 -0.025145  0.020361   
Avocado                     -0.960596  0.061173 -0.015270 -0.058410  0.127367   
Babaco                       0.977539  0.192721 -0.029874 -0.110653 -0.028688   
Babassu palm                -0.891986 -0.309275 -0.118454  0.020308 -0.094793   
Bagel                        0.996521 -0.089985  0.008190 -0.020626  0.010655   
Bakery Products              0.988138 -0.075058  0.010133  0.056164  0.075005   
Bamboo shoots               -0.902773 -0.293053 -0.118874 -0.013558 -0.033637   
Banana                      -0.806142  0.554776 -0.096327 -0.22362

In [58]:
final_dict = {}
max_min = {}

for word in food_characteristics_per_entity_reduced.index:
    nme = native_mexican_entities.copy()
    w = word
    t = get_similar_ingredients(w, food_characteristics_per_entity_reduced)
    top10 = t.sort_values(by=w, ascending=False).head(10)
    if w in nme:
        nme.remove(w)
    top10_mexican = t.loc[nme].sort_values(by=w, ascending=False).head(10)
    f = top10.index.to_list()
    f_mex = top10_mexican.index.to_list()
    final_dict[w] = [f, f_mex]
    
    max_min[w] = [top10.max(), top10.min()]
    #final_dict_99[w] = [t[t[w]>=0.99].index.to_list()] 
    #final_dict_95[w] = [t[(t[w]>=0.95) & (t[w]<0.99)].index.to_list()]
    #final_dict_90[w] = [t[(t[w]>=0.90) & (t[w]<0.95)].index.to_list()]
    #final_dict_80[w] = [t[(t[w]>=0.80) & (t[w]<0.90)].index.to_list()]

#food_characteristics_per_entity_reduced.loc[food_characteristics_per_entity_reduced.index!='Abalone']

In [57]:
pd.DataFrame(final_dict).T

0  \
Abalone                         [[American butterfish, Japanese chestnut, Taro, Arrowhead, Common salsify, Mexican groundcherry, Mountain yam, Horned melon, Devilfish, Narrowleaf cattail]]   
Abiyuch                                                                [[Skunk currant, Rowal, Deerberry, Mulberry, Black crowberry, Black huckleberry, Natal plum, Jicama, Jujube, Longan]]   
Acerola                                                                          [[Rose hip, Purple laver, Komatsuna, Longan, Kai lan, Sesbania flower, Jujube, Kale, Nance, Lambsquarters]]   
Acorn                                         [[Breadnut tree seed, Japanese chestnut, Oregon yampah, Prairie turnip, Taro, Arrowhead, Yautia, Common salsify, Mountain yam, Yardlong bean]]   
Adzuki bean                                                     [[Alfalfa, Pasta, Yam, Pak choy, Jerusalem artichoke, Chestnut, Millet, Japanese pumpkin, Purple mangosteen, Bamboo shoots]]   
Agar                                        [[Yardlong bean, Moth bean, Boysenberry, Sesbania flower, Winter squash, Malabar spinach, Jew's ear, Jicama, Alaska wild rhubarb, Mountain yam]]   
Agave                                                                             [[Great horned owl, Dates, Carob, Groundcherry, Rowal, Breadfruit, Sago palm, Irish moss, Nance, Abiyuch]]   
Alaska blackfish                                        [[Pacific rockfish, Spanish mackerel, Lemon sole, Atlantic menhaden, Striped mullet, Scup, Flatfish, Shark, Snapper, Northern pike]]   
Alaska pollock                                                      [[Pollock, Sockeye salmon, Elk, Orange roughy, Pacific ocean perch, Norway pout, Buffalo, Bison, Grouper, Green turtle]]   
Alaska wild rhubarb                                     [[Tinda, Nopal, Jicama, Horned melon, Mexican groundcherry, Narrowleaf cattail, Winter squash, Jew's ear, Natal plum, Mountain yam]]   
Albacore tuna                                [[Mallard duck, Soy cream, Beluga whale, Common carp, Pacific jack mackerel, Florida pompano, Byrsonima crassifolia, Tostada, Horchata, Kefir]]   
Alfalfa                                           [[Pak choy, Jerusalem artichoke, Bamboo shoots, Yam, Black salsify, Japanese pumpkin, Chayote, Purple mangosteen, Salmonberry, Persimmon]]   
Allspice                                                                                       [[Pepper, Rosemary, Lemon Balm, Nutmeg, Basil, Ginger, Star Anise, Laurel, Dill, Carom Seed]]   
Almond                                                                               [[Hazelnut, Brazil Nut, Pine, Cashew nut, Macadamia Nut, Pistachio, Peanut, Fenugreek, Pecans, Barley]]   
Alpinia                                     [[Byrsonima crassifolia, Apple Sauce, Soy cream, Skimmed Milk, Goat Milk, Malay Apple, Common carp, Heart of palm, Florida pompano, Sheep Milk]]   
Amaranth                                                                    [[Teff, Quinoa, Sorghum, Spelt, Triticale, Wild rice, Millet, Breadnut tree seed, Hard wheat, Annual wild rice]]   
American butterfish                          [[Japanese chestnut, Abalone, Ostrich fern, Arrowhead, Mexican groundcherry, Common salsify, Devilfish, Tree fern, Mountain yam, White lupine]]   
American shad               [[Striped mullet, Greenland halibut, Quail, Spanish mackerel, Chinook salmon, Scup, Yellowtail amberjack, Pacific rockfish, Alaska blackfish, Atlantic croaker]]   
Anchovy                            [[European anchovy, Pacific sardine, Yellowfin tuna, Chinook salmon, Quail, American shad, Chum salmon, Atlantic salmon, Pheasant, Yellowtail amberjack]]   
Anise                                                                                         [[Star Anise, Cumin, Carom Seed, Dill, Fennel, Turmeric, Cassia, Saffron, Tarragon, Cinnamon]]   
Annual wild rice                                                                       [[Wild rice, Red rice, Triticale, Hard wheat, Spelt, Amaranth, Teff,

In [60]:
#!mkdir ../data/external
pd.DataFrame(final_dict).T.rename(columns={0:'top10_ingredients', 1: 'top10_native_mexican_ingredients'}).to_csv('../data/external/Top10sustitutos_de_productos_with_mexican.csv')

In [117]:
#molecules_per_entity_reduced
#functional_groups_per_entity_reduced
#flavor_profile_per_entity_reduced

# How to include a new food-ingredient?
- 1) Search the molecules of the corresponding food, make an intersection of those molecules with the corresponding flavor molecules in the flavor molecules list. Then just take the intersection as a list of molecules. 
    - 1.1) For example: `new_ingredient: [flavor_molecule1, flavor_molecule2, ... flavor_moleculeN]`
    - 1.2) The best case scenario is that this ingredient can be found in [foodb](https://foodb.ca/), since it contains the molecules information of an ingredient, and only a rapid search must be done within the compounds and molecules that are founded there and the flavor_molecules_list that are found in flavordb. 
- 2) Get the nutritional information for the food, thinking on 100g of the ingredient. 
    - 2.1) The nutrients must be the same format as the one found in the [edamam's website](https://developer.edamam.com/food-database-api-docs) (in the Nutrient Guide section). 
    - 2.2) The best case scenario is that this ingredient can be found in [edammams api](https://developer.edamam.com/food-database-api-demo). 
